# MCS 275 Spring 2022 Worksheet 5

* Course instructor: Emily Dumas

## Topics

The main topics of this worksheet are:
* Context managers
* Debugging Python programs with
    * `print(...)`
    * `pdb`
    
**It's important to get some practice on each topic**, so for example, don't spend the entire lab period working on the context manager question.

Also, **please don't miss the opportunity to try out `pdb`**.  I think you can debug these puzzles by various methods, but it would be good to get some experience running a program in the debugger.

## Resources

These things might be helpful while working on the problems.  Remember that for worksheets,  we don't strictly limit what resources you can consult, so these are only suggestions.

* [Lecture 9 - More on decorators; context managers](https://www.dumas.io/teaching/2022/spring/mcs275/slides/lecture9.html)
* [Lecture 10 - Errors and debugging](https://www.dumas.io/teaching/2022/spring/mcs275/slides/lecture10.html)
* [Lecture 11 - pdb](https://www.dumas.io/teaching/2022/spring/mcs275/slides/lecture11.html)
* [MCS 275 Python Tour](https://www.dumas.io/teaching/2022/spring/mcs275/nbview/samplecode/python_tour.html)
* [Downey's book](https://greenteapress.com/thinkpython2/html/)
* MCS 260 course materials from Fall 2021:
    * [Slides, homework, worksheets, and projects](https://www.dumas.io/teaching/2021/fall/mcs260/)
    * [Sample programs](https://github.com/emilydumas/mcs260fall2021/tree/main/samplecode)


## 1. Fetch me a CSV file, please

This problem is about writing a context manager.  To remind you how these work, here is a context manager that makes sure a file with a given name exists when a `with` block starts.

In [39]:
import os

class EnsureExists:
    "Context manager that creates a file with a given name if it doesn't exist already"
    def __init__(self,fn):
        "Set the filename of the file to be created"
        self.fn = fn
    def __enter__(self):
        "Do the setup upon entering a with block: Create the file if needed"
        if not os.path.exists(self.fn):
            print("---EnsureExists is creating file '{}'".format(self.fn))
            open(self.fn,"w").close()
        else:
            print("---EnsureExists didn't need to to anything, as '{}' already exists'".format(self.fn))
    def __exit__(self,*args,**kwargs):
        "Called for cleanup upon leaving a with block; this context manager doesn't do any cleanup!"
        print("---EnsureExists is cleaning up (by doing nothing)")

Here's an example of using it.  Notice that inside the with-block, we can safely open the file for reading because the context manager created it.

In [40]:
with EnsureExists("sample.txt"):
    print("Checking if sample.txt exists:")
    if os.path.exists("sample.txt"):
        print("It does.")
    else:
        print("ERROR: It's missing!")
    with open("sample.txt","r") as infile:
        print("It contains {} characters.".format( len(infile.read()) ))

---EnsureExists is creating file 'sample.txt'
Checking if sample.txt exists:
It does.
It contains 0 characters.
---EnsureExists is cleaning up (by doing nothing)


And if we run the same code a second time, it will not need to create the file.

In [41]:
with EnsureExists("sample.txt"):
    print("Checking if sample.txt exists:")
    if os.path.exists("sample.txt"):
        print("It does.")
    else:
        print("ERROR: It's missing!")
    with open("sample.txt","r") as infile:
        print("It contains {} characters.".format( len(infile.read()) ))

---EnsureExists didn't need to to anything, as 'sample.txt' already exists'
Checking if sample.txt exists:
It does.
It contains 0 characters.
---EnsureExists is cleaning up (by doing nothing)


Using this example as a reference, make a new context manager called `TemporaryCSV` that generates a CSV file containing random data and writes it to a given filename.  That way, you can test code that works with a CSV file by wrapping it in a `with`-block using this context manager.  Use the class definition below as a starting point.

In [17]:
import csv
import os
import random

class TemporaryCSV:
    """
    Context manager that creates a CSV file with a given name containing some random data,
    optionally removing during cleanup.
    """
    def __init__(self,fn,columns=3,rows=5,header=True,remove=False):
        """
        Setup context manager that will create a CSV file named `fn` upon entering the `with`-block,
        containing `columns` columns and `rows` rows of random integers.  If `header` is True, also write
        some random strings as column headers.
        
        If `remove` is True (the default), the CSV file is deleted at the end of the `with`-block.
        """

    def __enter__(self):
        "Create the CSV"
        # YOU WRITE THIS METHOD!
        
    def __exit__(self,*args,**kwargs):  # There are specific arguments passed here, but let's not worry about them
        "Remove the CSV if configured to do so"
        # YOU WRITE THIS METHOD!

Here's an example of what using the final context manager should look like:

In [33]:
import csv

# A sample function to use on a CSV file
def csv_stats(fn):
    "Return stats about a CSV file"
    rowcount = 0
    with open(fn,"r",newline="",encoding="UTF-8") as infile:
        rdr = csv.DictReader(infile)
        for row in rdr:
            rowcount += 1
            colnames = list(row.keys())
    return {"rowcount":rowcount, "colnames":colnames}


with TemporaryCSV("temp.csv",columns=2,rows=10,remove=True):
    d = csv_stats("temp.csv")
    print("Found the CSV file to have {} rows and {} columns, named {}".format(
        d["rowcount"],
        len(d["colnames"]),
        ", ".join( "'{}'".format(s) for s in d["colnames"])
    ))
    
if not os.path.exists("temp.csv"):
    print("And hey, the CSV file is gone now.")

Found the CSV file to have 10 rows and 2 columns, named 'GoRYG', 'mTsOd'
And hey, the CSV file is gone now.


## 2. Broken vending machine

Download the Python program linked below. 

* [vend.py](https://raw.githubusercontent.com/emilydumas/mcs275spring2022/master/samplecode/debugging/worksheet/vend.py)

It simulates a vending machine, and is similar to a project assigned in MCS 260 in Fall 2020.  Run it, use the "help" command in its text interface to learn about the available commands, and try them out.

This script has a bug which affects certain purchases.  For example, try starting the script and depositing \\$1.15 as four quarters, one dime, and one nickel, and then selecting item 4 (costing \\$1.10).  The expected behavior would be: The item is purchased, and \\$0.05 is given in change.  Instead, the script will get stuck (and may require you to press Control-C in the terminal to exit).

Debug the program using an active debugging technique (`print(...)` or `pdb`) and find the cause of the infinite loop that prevents the program from executing as intended.  Devise and test a fix.

## 3. Is this function misbehaving?

The function below is supposed to compute the character histogram of a string, with the option to update an existing histogram so that a large text can be processed in chunks.  However, it doesn't work: As you'll see form the example code, it doesn't start from a blank histogram in some cases.  Why not?

Use debugging techniques to find the first place where the behavior of the function differs from the documented intention of the programmer.

In [38]:
"""Histogram example for debugging"""
# MCS 275 Spring 2022 - Emily Dumas

def update_char_histogram(s,hist = dict()):
    """
    Make a dictionary mapping letters to the number of times they occur in string `s`, i.e.
    a histogram.  If `hist` is provided, assume this is an existing histogram that should be
    updated (incremented) to account for the additional letters in `s`.  Thus, for example,
    this function could be called once for each line of a text file to incrementally compute
    a histogram of the entire file with needing to read the entire file into memory.
    """
    for c in s:
        if c.isspace():
            continue
        if c not in hist:
            hist[c] = 0
        hist[c] += 1
    return hist


# Develop a histogram in two steps
print("Histogram of 'laser-wielding maniac':")
h = update_char_histogram("laser-wielding maniac") # no hist given, so start from scratch
print(h)
print("Histogram of previous line and 'creeping dread of infinitely dividing bacteria':")
h = update_char_histogram("creeping dread of infinitely dividing bacteria",h)
print(h)

# Start from scratch again, develop a new histogram
print("Histogram of the word 'silent sea':") # no hist given, so start from scratch
h = update_char_histogram("silent sea")
print(h) # Why does it think there are twelve "i"s in "silent sea"?!?!

Histogram of 'laser-wielding maniac':
{'l': 2, 'a': 3, 's': 1, 'e': 2, 'r': 1, '-': 1, 'w': 1, 'i': 3, 'd': 1, 'n': 2, 'g': 1, 'm': 1, 'c': 1}
Histogram of previous line and 'creeping dread of infinitely dividing bacteria':
{'l': 3, 'a': 6, 's': 1, 'e': 7, 'r': 4, '-': 1, 'w': 1, 'i': 11, 'd': 5, 'n': 6, 'g': 3, 'm': 1, 'c': 3, 'p': 1, 'o': 1, 'f': 2, 't': 2, 'y': 1, 'v': 1, 'b': 1}
Histogram of the word 'silent sea':
{'l': 4, 'a': 7, 's': 3, 'e': 9, 'r': 4, '-': 1, 'w': 1, 'i': 12, 'd': 5, 'n': 7, 'g': 3, 'm': 1, 'c': 3, 'p': 1, 'o': 1, 'f': 2, 't': 3, 'y': 1, 'v': 1, 'b': 1}


## 4. Tic-tac-toe too easily won

Download the program:

* [ttt.py](https://raw.githubusercontent.com/emilydumas/mcs275spring2022/master/samplecode/debugging/worksheet/ttt.py)

It is a tic-tac-toe game: two players take turns placing 'X' or 'O' on a 3x3 board.  The first player to get 3 in a row horizontally, vertically, or diagonally wins.

But this game has a strange bug: No matter where the first player puts their 'X', they win.

Use debugging techniques to find the first place where the behavior of the program differs from the programmer's intention, and to fix it.

Note: This example was based on a collection of unintuitive Python language behaviors collected by 
Satwik Kansal.  The URL for that source document is included below, but be warned, it contains spoilers for this problem (and some crude language).  Opening the page is not recommended until after discussion is over:
* `https://github.com/satwikkansal/wtfpython#-a-tic-tac-toe-where-x-wins-in-the-first-attempt`